This notebook reproduces the example from scDesign package: [Simulate spatial transcriptomic data](https://songdongyuan1994.github.io/scDesign3/docs/articles/scDesign3-spatial-vignette.html)

In [1]:
import anndata
import os
import requests

save_path = "data/stxBrain.h5ad"
if not os.path.exists(save_path):
    response = requests.get("https://go.wisc.edu/o1y03l")
    with open(save_path, "wb") as f:
        f.write(response.content)

example_sce = anndata.read_h5ad(save_path)

In [2]:
example_sce = example_sce[:, :10].to_memory()
example_sce.obs

orig.ident  nCount_Spatial  nFeature_Spatial  slice  \
AAACAAGTATCTCCCA-1  anterior1         13069.0              4242    1.0   
AAACACCAATAACTGC-1  anterior1         37448.0              7860    1.0   
AAACAGAGCGACTCCT-1  anterior1         28475.0              6332    1.0   
AAACAGCTTTCAGAAG-1  anterior1         39718.0              7957    1.0   
AAACAGGGTCTATATT-1  anterior1         33392.0              7791    1.0   
...                       ...             ...               ...    ...   
TTGTGTTTCCCGAAAG-1  anterior1         27417.0              6539    1.0   
TTGTTCAGTGTGCTAC-1  anterior1         29222.0              6388    1.0   
TTGTTGTGTGTCAAGA-1  anterior1         22285.0              5747    1.0   
TTGTTTCACATCCAGG-1  anterior1         16724.0              4371    1.0   
TTGTTTCCATACAACT-1  anterior1         16006.0              4704    1.0   

                      region  nCount_SCT  nFeature_SCT SCT_snn_res.0.8  \
AAACAAGTATCTCCCA-1  anterior     23817.0          4710               2   
AAACACCAATAACTGC-1  anterior     25085.0          7425               5   
AAACAGAGCGACTCCT-1  anterior     25455.0          6326               3   
AAACAGCTTTCAGAAG-1  anterior     24862.0          7326              11   
AAACAGGGTCTATATT-1  anterior     25288.0          7673              11   
...                      ...         ...           ...             ...   
TTGTGTTTCCCGAAAG-1  anterior     25422.0          6537               1   
TTGTTCAGTGTGCTAC-1  anterior     25381.0          6386               6   
TTGTTGTGTGTCAAGA-1  anterior     23705.0          5745               1   
TTGTTTCACATCCAGG-1  anterior     23607.0          4483               4   
TTGTTTCCATACAACT-1  anterior     23613.0          4830               4   

                   seurat_clusters  spatial1  spatial2 cell_type  
AAACAAGTATCTCCCA-1               2      7475      8501         2  
AAACACCAATAACTGC-1               5      8553      2788         5  
AAACAGAGCGACTCCT-1               3      3164      7950         3  
AAACAGCTTTCAGAAG-1              11      6637      2099        11  
AAACAGGGTCTATATT-1              11      7116      2375        11  
...                            ...       ...       ...       ...  
TTGTGTTTCCCGAAAG-1               1      7595      5541         1  
TTGTTCAGTGTGCTAC-1               6      4362      5885         6  
TTGTTGTGTGTCAAGA-1               1      5200      6780         1  
TTGTTTCACATCCAGG-1               4      8434      4371         4  
TTGTTTCCATACAACT-1               4      6877      3338         4  

[2696 rows x 12 columns]

This is not quite the simulator used in the scDesign3 vignette, because we are using the same copula correlation across all groups. We need a version of negative_binomial_copula that takes a grouping variable in the formula as well.

In [3]:
from scdesigner.experimental.estimators import negative_binomial_copula

formula = "~ bs(spatial1, df=100) * bs(spatial2, df=100)"
params = negative_binomial_copula(example_sce, formula)

In [4]:
from scdesigner.experimental.samplers import negative_binomial_copula_sample

simulated = negative_binomial_copula_sample(params, example_sce.obs, formula)

In [5]:
import altair
from scdesigner.experimental.diagnose import plot_umap
altair.data_transformers.enable("vegafusion")

combined = anndata.concat({"real": example_sce, "sim": simulated}, label="source")
plot_umap(combined, color="seurat_clusters", facet="source", n_comps=5)

alt.FacetChart(...)

In [6]:
import pandas as pd
import numpy as np

def plot_spatial(adata, spatial_names=["spatial1", "spatial2"]):
    plot_df = pd.concat([
        adata.obs[spatial_names].reset_index(drop=True), 
        pd.DataFrame(np.log1p(adata.X)).reset_index(drop=True)
    ], axis=1)

    plot_df.columns = spatial_names + list(adata.var_names)

    plot_df_melted = plot_df.melt(id_vars=spatial_names, var_name="gene", value_name="expression")
    return altair.Chart(plot_df_melted).mark_point(size=1).encode(
        x=spatial_names[0],
        y=spatial_names[1],
        fill=altair.Fill("expression", scale=altair.Scale(scheme="viridis")),
        color=altair.Color("expression", scale=altair.Scale(scheme="viridis"))
    ).properties(width=200, height=200)\
    .facet(facet="gene", columns=5)

In [7]:
plot_spatial(example_sce)

alt.FacetChart(...)

In [8]:
plot_spatial(simulated)

alt.FacetChart(...)